# Census Data Tools

MORPC works regularly with census data, including but not limited to ACS 5 and 1-year, Decennial Census, PEP, and geographies. The following module is useful for gathering and organizing census data for processes in various workflow. Those workflows are linked when appropriate. 

In [4]:
import morpc

## API functions and variables

api_get() is a low-level wrapper for Census API requests that returns the results as a pandas dataframe. If necessary, it splits the request into several smaller requests to bypass the 50-variable limit imposed by the API.  

The resulting dataframe is indexed by GEOID (regardless of whether it was requested) and omits other fields that are not requested but which are returned automatically with each API request (e.g. "state", "county") 

In [5]:
url = 'https://api.census.gov/data/2022/acs/acs1'
params = {
    "get": "GEO_ID,NAME,B01001_001E",
    "for": "county:049,041",
    "in": "state:39"
}

In [6]:
api = morpc.census.api_get(url, params)

Total variables requested: 3
Starting request #1. 3 variables remain.


In [7]:
api

NAME B01001_001E
GEO_ID                                           
0500000US39041  Delaware County, Ohio      226296
0500000US39049  Franklin County, Ohio     1321820

## American Community Survey (ACS) Data Class

When using ACS data, generally we will be digesting data produded using the [morpc-censusacs-fetch](https://github.com/morpc/morpc-censusacs-fetch) workflow. The data that is produced from that script is by default saved in its output_data folders ./morpc-censusacs-fetch/output_data/

The Census ACS Fetch script leverages the `acs_data` class form `morpc.census`


### Create an initial object which represents a variable in the ACS data api.

The class takes 3 arguments:

1. variable group number
2. the year
3. the type of survey (1 or 5 year estimates)

In [8]:
import morpc

In [9]:
acs = morpc.census.acs_data('B02001', '2023', '5')

The initial call creates queries the Census for the variable definitions and returns a dictionary of the available variables in the group. see `acs.VARS`

In [10]:
acs.VARS

{'B02001_001E': {'label': 'Estimate!!Total:',
  'concept': 'Race',
  'predicateType': 'int',
  'group': 'B02001',
  'limit': 0,
  'attributes': 'B02001_001EA,B02001_001M,B02001_001MA'},
 'B02001_002E': {'label': 'Estimate!!Total:!!White alone',
  'concept': 'Race',
  'predicateType': 'int',
  'group': 'B02001',
  'limit': 0,
  'attributes': 'B02001_002EA,B02001_002M,B02001_002MA'},
 'B02001_003E': {'label': 'Estimate!!Total:!!Black or African American alone',
  'concept': 'Race',
  'predicateType': 'int',
  'group': 'B02001',
  'limit': 0,
  'attributes': 'B02001_003EA,B02001_003M,B02001_003MA'},
 'B02001_004E': {'label': 'Estimate!!Total:!!American Indian and Alaska Native alone',
  'concept': 'Race',
  'predicateType': 'int',
  'group': 'B02001',
  'limit': 0,
  'attributes': 'B02001_004EA,B02001_004M,B02001_004MA'},
 'B02001_005E': {'label': 'Estimate!!Total:!!Asian alone',
  'concept': 'Race',
  'predicateType': 'int',
  'group': 'B02001',
  'limit': 0,
  'attributes': 'B02001_005E

The initial call alse fetchs a list of dimensions from a cached json file in ./morpc/census/acs_variable_group.json and is stored in morpc.census.ACS_VAR_GROUPS.

#### Manual verfication for variable dimension names. 

The list of dimensions are automatically created from the Census Variable labels and need verified before being used. If the dimesion names have not be verified, the will not be stored. Navigate to the JSON and check to make sure that there are the correct number of dimension and that they are in the correct order. Change the verfication field to `true`.

In [11]:
acs.DIMENSIONS

['TOTAL', 'Race', 'Two or More Races']

### Query the API for the deisred variables and geography

The `.query()` method queries the API and caches the data in memory under `acs.DATA`. At the same time it creates a frictionless schema that corrosponds with the data. 

#### scope:
These are pre-defined sumlevels and scopes for commonly queried geographies. see `morpc.census.SCOPES`.

In [12]:
morpc.census.SCOPES

{'us-states': {'desc': 'all states in the United States', 'for': 'state:*'},
 'ohio': {'desc': 'the State of Ohio', 'for': 'state:39'},
 'ohio-counties': {'desc': 'all counties in the State of Ohio',
  'for': 'county:*',
  'in': 'state:39'},
 'ohio-tracts': {'desc': 'all Census tracts in the State of Ohio',
  'for': 'tract:*',
  'in': 'state:39'},
 'region15-counties': {'desc': 'all counties in the MORPC 15-county region',
  'for': 'county:041,045,049,089,097,129,159,083,101,117,047,073,091,127,141',
  'in': 'state:39'},
 'region15-tracts': {'desc': 'all Census tracts in the MORPC 10-county region',
  'for': 'tract:*',
  'in': ['state:39',
   'county:041,045,049,089,097,129,159,083,101,117,047,073,091,127,141']},
 'regionmpo-parts': {'desc': 'all Census township parts and place parts that are MORPC MPO members',
  'ucgid': '1550000US3902582041,0700000US390410577499999,0700000US390410578899999,0700000US390410942899999,1550000US3918000041,0700000US390411814099999,1550000US3921434041,0700

In [13]:
acs = acs.query(scope='region15-tracts')

morpc-acs5-2023-region15-tracts-b02001 schema is valid
Total variables requested: 22
Starting request #1. 22 variables remain.
Starting request #2. 3 variables remain.
morpc.frictionless.load_data | INFO | Loading Frictionless Resource file at location ..\..\morpc-geos-collect\output_data\morpc-geos.resource.yaml
morpc.frictionless.load_data | INFO | Ignoring schema as directed by useSchema parameter.
morpc.frictionless.load_data | INFO | Loading data, resource file, and schema (if applicable) from their source locations
morpc.frictionless.load_data | INFO | --> Data file: ..\..\morpc-geos-collect\output_data\morpc-geos.gpkg
morpc.frictionless.load_data | INFO | --> Resource file: ..\..\morpc-geos-collect\output_data\morpc-geos.resource.yaml
morpc.frictionless.load_data | INFO | --> Schema file: Not available. Ignoring schema.
morpc.frictionless.load_data | INFO | Loading data.
morpc.frictionless.load_data | INFO | Skipping casting of field types since we are ignoring schema.


C:\Users\jinskeep\morpc_venv\Lib\site-packages\pyogrio\raw.py:198: RuntimeWarning: driver GPKG does not support open option DRIVER


In [14]:
data = acs.DATA
data.head()

NAME  B02001_001E  \
GEO_ID                                                                          
1400000US39041010100     Census Tract 101; Delaware County; Ohio         5257   
1400000US39041010200     Census Tract 102; Delaware County; Ohio         5865   
1400000US39041010420  Census Tract 104.20; Delaware County; Ohio         2926   
1400000US39041010421  Census Tract 104.21; Delaware County; Ohio         2811   
1400000US39041010422  Census Tract 104.22; Delaware County; Ohio         6368   

                      B02001_001M  B02001_002E  B02001_002M  B02001_003E  \
GEO_ID                                                                     
1400000US39041010100          526         4460          518          285   
1400000US39041010200          639         4502          617          239   
1400000US39041010420          232         2539          271          159   
1400000US39041010421          418         2609          393          107   
1400000US39041010422          662         5218          771          212   

                      B02001_003M  B02001_004E  B02001_004M  B02001_005E  ...  \
GEO_ID                                                                    ...   
1400000US39041010100          130            1            2          120  ...   
1400000US39041010200          232            0           18          342  ...   
1400000US39041010420          152            0           13           22  ...   
1400000US39041010421          130            0           13            0  ...   
1400000US39041010422          184            0           18           72  ...   

                      B02001_006E  B02001_006M  B02001_007E  B02001_007M  \
GEO_ID                                                                     
1400000US39041010100            0           18           51           53   
1400000US39041010200            0           18           35           56   
1400000US39041010420            0           13           11           17   
1400000US39041010421            0           13           42           39   
1400000US39041010422           35           48           46           76   

                      B02001_008E  B02001_008M  B02001_009E  B02001_009M  \
GEO_ID                                                                     
1400000US39041010100          340          136           85           82   
1400000US39041010200          747          293          525          305   
1400000US39041010420          195          112           89           68   
1400000US39041010421           53           53           33           49   
1400000US39041010422          785          325          429          268   

                      B02001_010E  B02001_010M  
GEO_ID                                          
1400000US39041010100          255          105  
1400000US39041010200          222          175  
1400000US39041010420          106          107  
1400000US39041010421           20           28  
1400000US39041010422          356          219  

[5 rows x 21 columns]

### For custom queries, use for and in parameters to pass to api query. 

#### for_param:
(optional) The geographies for which to call the the query "state:*" represents all states. "state:39" represent Ohio.

#### in_param:
(optional) A filter for the for parameter. In combinations this allows you do call for small geograhpies inside larger ones. 

> Examples: for_param="county:\*", in_param="state:39" would get all counties in Ohio.
> for_param="tract:\*", in_param='state:39,county:041,049' gets all census tracts in Delaware and Franklin Counties.

### Filter the variables using the get parameter

#### get_param:
(Optional) If you want to return a subset of variables, they can be passed here as a list.

### Dimension Tables

When the query is called the class makes table with the dimensions included that can be used to get summaries of the data. 

This can be used to get quick queries for summaries. 

In [15]:
acs = morpc.census.acs_data('B02001', '2023', '5').query(scope='region15-tracts')

morpc-acs5-2023-region15-tracts-b02001 schema is valid
Total variables requested: 22
Starting request #1. 22 variables remain.
Starting request #2. 3 variables remain.
morpc.frictionless.load_data | INFO | Loading Frictionless Resource file at location ..\..\morpc-geos-collect\output_data\morpc-geos.resource.yaml
morpc.frictionless.load_data | INFO | Ignoring schema as directed by useSchema parameter.
morpc.frictionless.load_data | INFO | Loading data, resource file, and schema (if applicable) from their source locations
morpc.frictionless.load_data | INFO | --> Data file: ..\..\morpc-geos-collect\output_data\morpc-geos.gpkg
morpc.frictionless.load_data | INFO | --> Resource file: ..\..\morpc-geos-collect\output_data\morpc-geos.resource.yaml
morpc.frictionless.load_data | INFO | --> Schema file: Not available. Ignoring schema.
morpc.frictionless.load_data | INFO | Loading data.
morpc.frictionless.load_data | INFO | Skipping casting of field types since we are ignoring schema.


C:\Users\jinskeep\morpc_venv\Lib\site-packages\pyogrio\raw.py:198: RuntimeWarning: driver GPKG does not support open option DRIVER


In [16]:
acs.DIM_TABLE.LONG

GEO_ID                                        NAME  \
0      1400000US39041010100     Census Tract 101; Delaware County; Ohio   
1      1400000US39041010200     Census Tract 102; Delaware County; Ohio   
2      1400000US39041010420  Census Tract 104.20; Delaware County; Ohio   
3      1400000US39041010421  Census Tract 104.21; Delaware County; Ohio   
4      1400000US39041010422  Census Tract 104.22; Delaware County; Ohio   
...                     ...                                         ...   
11655  1400000US39159050502     Census Tract 505.02; Union County; Ohio   
11656  1400000US39159050601     Census Tract 506.01; Union County; Ohio   
11657  1400000US39159050602     Census Tract 506.02; Union County; Ohio   
11658  1400000US39159050701     Census Tract 507.01; Union County; Ohio   
11659  1400000US39159050702     Census Tract 507.02; Union County; Ohio   

          VARIABLE  VALUE  VAR_TYPE  TOTAL               Race  \
0      B02001_001E   5257  Estimate  Total              Total   
1      B02001_001E   5865  Estimate  Total              Total   
2      B02001_001E   2926  Estimate  Total              Total   
3      B02001_001E   2811  Estimate  Total              Total   
4      B02001_001E   6368  Estimate  Total              Total   
...            ...    ...       ...    ...                ...   
11655  B02001_010M    161       MOE  Total  Two or More Races   
11656  B02001_010M     89       MOE  Total  Two or More Races   
11657  B02001_010M     70       MOE  Total  Two or More Races   
11658  B02001_010M     80       MOE  Total  Two or More Races   
11659  B02001_010M     65       MOE  Total  Two or More Races   

                                       Two or More Races REFERENCE_YEAR  
0                                                  Total           2023  
1                                                  Total           2023  
2                                                  Total           2023  
3                                                  Total           2023  
4                                                  Total           2023  
...                                                  ...            ...  
11655  Two races excluding Some Other Race, and three...           2023  
11656  Two races excluding Some Other Race, and three...           2023  
11657  Two races excluding Some Other Race, and three...           2023  
11658  Two races excluding Some Other Race, and three...           2023  
11659  Two races excluding Some Other Race, and three...           2023  

[11660 rows x 9 columns]

In [17]:
acs.DIM_TABLE.WIDE

GEO_ID                                                                                                                 1400000US39041010100  \
NAME                                                                                                Census Tract 101; Delaware County; Ohio   
REFERENCE_YEAR                                                                                                                         2023   
Race                                             Two or More Races                                                                            
Total                                            Total                                                                                 5257   
White alone                                      Total                                                                                 4460   
Black or African American alone                  Total                                                                                  285   
American Indian and Alaska Native alone          Total                                                                                    1   
Asian alone                                      Total                                                                                  120   
Native Hawaiian and Other Pacific Islander alone Total                                                                                    0   
Some Other Race alone                            Total                                                                                   51   
Two or More Races                                Total                                                                                  340   
                                                 Two races including Some Other Race                                                     85   
                                                 Two races excluding Some Other Race, and three ...                                     255   

GEO_ID                                                                                                                 1400000US39041010200  \
NAME                                                                                                Census Tract 102; Delaware County; Ohio   
REFERENCE_YEAR                                                                                                                         2023   
Race                                             Two or More Races                                                                            
Total                                            Total                                                                                 5865   
White alone                                      Total                                                                                 4502   
Black or African American alone                  Total                                                                                  239   
American Indian and Alaska Native alone          Total                                                                                    0   
Asian alone                                      Total                                                                                  342   
Native Hawaiian and Other Pacific Islander alone Total                                                                                    0   
Some Other Race alone                            Total                                                                                   35   
Two or More Races                                Total                                                                                  747   
                                                 Two races including Some Other Race                                                    525   
                                                 Two races excluding Some Other Race, and three ...                                     22

In [18]:
acs.DIM_TABLE.PERCENT

Race                                                                           White alone  \
Two or More Races                                                                    Total   
GEO_ID               NAME                                       REFERENCE_YEAR               
1400000US39041010100 Census Tract 101; Delaware County; Ohio    2023             84.839262   
1400000US39041010200 Census Tract 102; Delaware County; Ohio    2023             76.760443   
1400000US39041010420 Census Tract 104.20; Delaware County; Ohio 2023             86.773753   
1400000US39041010421 Census Tract 104.21; Delaware County; Ohio 2023             92.813945   
1400000US39041010422 Census Tract 104.22; Delaware County; Ohio 2023             81.940955   
...                                                                                    ...   
1400000US39159050502 Census Tract 505.02; Union County; Ohio    2023             88.669528   
1400000US39159050601 Census Tract 506.01; Union County; Ohio    2023             71.247834   
1400000US39159050602 Census Tract 506.02; Union County; Ohio    2023             88.611544   
1400000US39159050701 Census Tract 507.01; Union County; Ohio    2023             93.212575   
1400000US39159050702 Census Tract 507.02; Union County; Ohio    2023             82.721663   

Race                                                                           Black or African American alone  \
Two or More Races                                                                                        Total   
GEO_ID               NAME                                       REFERENCE_YEAR                                   
1400000US39041010100 Census Tract 101; Delaware County; Ohio    2023                                  5.421343   
1400000US39041010200 Census Tract 102; Delaware County; Ohio    2023                                  4.075021   
1400000US39041010420 Census Tract 104.20; Delaware County; Ohio 2023                                  5.434040   
1400000US39041010421 Census Tract 104.21; Delaware County; Ohio 2023                                  3.806475   
1400000US39041010422 Census Tract 104.22; Delaware County; Ohio 2023                                  3.329146   
...                                                                                                        ...   
1400000US39159050502 Census Tract 505.02; Union County; Ohio    2023                                  0.000000   
1400000US39159050601 Census Tract 506.01; Union County; Ohio    2023                                  4.098787   
1400000US39159050602 Census Tract 506.02; Union County; Ohio    2023                                  0.557165   
1400000US39159050701 Census Tract 507.01; Union County; Ohio    2023                                  1.707266   
1400000US39159050702 Census Tract 507.02; Union County; Ohio    2023                                  3.410198   

Race                                                                           American Indian and Alaska Native alone  \
Two or More Races                                                                                                Total   
GEO_ID               NAME                                       REFERENCE_YEAR                                           
1400000US39041010100 Census Tract 101; Delaware County; Ohio    2023                                          0.019022   
1400000US39041010200 Census Tract 102; Delaware County; Ohio    2023                                          0.000000   
1400000US39041010420 Census Tract 104.20; Delaware County; Ohio 2023                                          0.000000   
1400000US39041010421 Census Tract 104.21; Delaware County; Ohio 2023                                          0.000000   
1400000US39041010422 Census Tract 104.22; Delaware County; Ohio 2023                                          0.000000   
...                                                                                                           

### Save raw data (not dim table) as a frictionless resource with schema

After querying the data, save the data as a frictionless resource with reasonable descriptors. 

In [19]:
acs.save(output_dir='./temp_data/')

Resource is valid.


In [20]:
acs.SCHEMA

{'fields': [{'name': 'GEO_ID',
             'type': 'string',
             'description': 'Unique identifier for geography'},
            {'name': 'NAME',
             'type': 'string',
             'description': 'Name of the geography'},
            {'name': 'B02001_001E',
             'type': 'integer',
             'description': 'Estimate!!Total: | Race | Estimate'},
            {'name': 'B02001_001M',
             'type': 'integer',
             'description': 'Estimate!!Total: | Race | MOE'},
            {'name': 'B02001_002E',
             'type': 'integer',
             'description': 'Estimate!!Total:!!White alone | Race | Estimate'},
            {'name': 'B02001_002M',
             'type': 'integer',
             'description': 'Estimate!!Total:!!White alone | Race | MOE'},
            {'name': 'B02001_003E',
             'type': 'integer',
             'description': 'Estimate!!Total:!!Black or African American alone '
                            '| Race | Estimate'},
     

In [21]:
acs.RESOURCE

{'name': 'morpc-acs5-2023-region15-tracts-b02001',
 'type': 'table',
 'title': '2023 American Community Survey 5-Year Estimates For All Census '
          'Tracts In The Morpc 10-County Region.',
 'description': 'Selected variables from 2023 ACS 5-Year estimates for all '
                'Census tracts in the MORPC 10-county region. Data was '
                'retrieved 2025-07-16',
 'profile': 'tabular-data-resource',
 'sources': [{'title': '2023 American Community Survey 5-Year Estimates, U.S. '
                       'Census Bureau',
              'path': 'https://api.census.gov/data/2023/acs/acs5',
              '_params': {'get': 'GEO_ID,NAME,B02001_001E,B02001_001M,B02001_002E,B02001_002M,B02001_003E,B02001_003M,B02001_004E,B02001_004M,B02001_005E,B02001_005M,B02001_006E,B02001_006M,B02001_007E,B02001_007M,B02001_008E,B02001_008M,B02001_009E,B02001_009M,B02001_010E,B02001_010M',
                          'for': 'tract:*',
                          'in': ['state:39',
             

## Load data from cached file

In [22]:
acs = morpc.census.acs_data('B02001', '2023', '5').load(scope='region15-counties', dirname='./temp_data/')

morpc.frictionless.load_data | INFO | Loading Frictionless Resource file at location morpc-acs5-2023-region15-counties-b02001.resource.yaml
morpc.frictionless.load_data | INFO | Using schema path specified in resource file.
morpc.frictionless.load_data | INFO | Loading data, resource file, and schema (if applicable) from their source locations
morpc.frictionless.load_data | INFO | --> Data file: morpc-acs5-2023-region15-counties-b02001.csv
morpc.frictionless.load_data | INFO | --> Resource file: morpc-acs5-2023-region15-counties-b02001.resource.yaml
morpc.frictionless.load_data | INFO | --> Schema file: morpc-acs5-2023-region15-counties-b02001.schema.yaml
morpc.frictionless.load_data | INFO | Loading data.
morpc.frictionless.load_data | INFO | Loading Frictionless Resource file at location ..\..\morpc-geos-collect\output_data\morpc-geos.resource.yaml
morpc.frictionless.load_data | INFO | Ignoring schema as directed by useSchema parameter.
morpc.frictionless.load_data | INFO | Loading d

C:\Users\jinskeep\morpc_venv\Lib\site-packages\pyogrio\raw.py:198: RuntimeWarning: driver GPKG does not support open option DRIVER


## Georeference the data to map

Add geometries by joining GEOS to DATA.

In [23]:
acs.GEOS

geometry
GEO_ID                                                           
0500000US39041  POLYGON ((1823116.85 881478.815, 1823475.64 88...
0500000US39045  POLYGON ((1971222.637 605224.176, 1971196.493 ...
0500000US39047  POLYGON ((1721811.474 502868.808, 1721795.426 ...
0500000US39049  POLYGON ((1769714.921 754470.125, 1769772.783 ...
0500000US39073  POLYGON ((1996131.846 506358.095, 1996002.396 ...
0500000US39083  POLYGON ((2055376.301 868263.698, 2055374.748 ...
0500000US39089  POLYGON ((1978895.534 817764.245, 1978931.268 ...
0500000US39091  POLYGON ((1550541.342 907938.451, 1551948.024 ...
0500000US39097  POLYGON ((1757251.035 731172.882, 1757187.521 ...
0500000US39101  POLYGON ((1777627.41 984998.588, 1778487.147 9...
0500000US39117  POLYGON ((1929286.936 880630.026, 1929032.53 8...
0500000US39127  POLYGON ((1976263.31 669748.55, 1976258.806 66...
0500000US39129  POLYGON ((1871811.429 568901.93, 1871832.568 5...
0500000US39141  POLYGON ((1827878.347 539450.706, 1827900.921 ...
0500000US39159  POLYGON ((1780972.381 801308.987, 1780979.398 ...

In [24]:
import geopandas as gpd
acs.DATA = gpd.GeoDataFrame(acs.DATA.join(acs.GEOS), geometry='geometry')

In [25]:
acs.DATA.explore()

## Use the built in .MAP to view a map of all the columns in data

In [26]:
acs.MAP

## Below should still be functional, but hoping to implement into ACS class

#### Load the data using frictionless.load_data()

In [ ]:
data, resource, schema = morpc.frictionless.load_data('./temp_data/morpc-acs5-2023-state-B01001.resource.yaml', verbose=False)

#### Using ACS_ID_FIELDS to get the fields ids

In [ ]:
morpc.census.acs_generate_universe_table(data.set_index("GEO_ID"), "B01001_001")

#### Create a dimension table with the data and the dimension names

In [ ]:
dim_table = morpc.census.acs_generate_dimension_table(data.set_index("GEO_ID"), schema, idFields=idFields, dimensionNames=["Sex", "Age group"])

In [ ]:
dim_table.loc[dim_table['Variable type'] == 'Estimate'].head()

### Build ACS Variable Group JSON for Dimension names

In [ ]:
import requests
r = requests.get('https://api.census.gov/data/2023/acs/acs5/variables.json')
varjson = r.json()

In [ ]:
groups = {}
for variable in varjson['variables']:
    if variable not in ['for', 'in', 'ucgid', 'GEO_ID', 'AIANHH', 'AIHHTL', 'AIRES', 'ANRC']:
        group = varjson['variables'][variable]['group']
        if not group[-1].isalpha():
            if group not in groups:
                groups[group] = {}
                groups[group]['concept'] = varjson['variables'][variable]['concept'].replace('Year and Over','Year & Over').replace('Indian and Alaska','Indian & Alaska').replace('Hawaiian and Other','Hawaiian & Other')
                groups[group]['dimensions'] = ['TOTAL'] + varjson['variables'][variable]['concept'].replace(' by ',':').replace('Year and Over','Year & Over').replace('Indian and Alaska','Indian & Alaska').replace('Hawaiian and Other','Hawaiian & Other').replace(' and ',':').split(':')
                groups[group]['dimensions_verified'] = False
                variables = {}
                for variable in varjson['variables']:
                    if varjson['variables'][variable]['group'] == group:
                        variables[variable] = varjson['variables'][variable]['label']
                variables = {k: v for k, v in sorted(variables.items(), key=lambda item: item[0])}
                groups[group]['variables'] = variables

In [ ]:
groups = {k: v for k, v in sorted(groups.items(), key=lambda item: item[0])}

In [ ]:
import json
with open('../morpc/census/acs_variable_groups.json', 'w') as file:
    json.dump(groups, file, indent=3)